### Earth Engine Objects Visualization using Folium
**Author:** René Kopeinig<br>
**Description:** Visualization of Earth Engine Objects (e.g. Image, Image Collection, Feature and Feature Collection) using Folium.

In [1]:
%matplotlib inline

In [2]:
import ee, datetime, folium, requests, geextract
import pandas as pd
from IPython.display import Image
from pylab import *
import matplotlib.pyplot as plt
import seaborn as sns
import geopandas as gpd
from folium.plugins import HeatMap
from ipyleaflet import *

ee.Initialize()

#### Create Function for adding layers to Google Earth Engine
Firstly, we have to create the function which is capable of adding raster layers to Google Earth Engine. 
So far I have only found a way to add ee.Image objects. I also found out that not all ee.Image objects are possible to load into a Folium map. I couldn't manage to load Sentinel or Landsat imagery.

In [3]:
def add_earth_engine_layer(self, imageObject, vis, layer_name):
    dict_mapId = ee.Image(imageObject).getMapId(vis)
    folium.raster_layers.TileLayer(
        tiles = dict_mapId['tile_fetcher'].url_format,
        min_zoom=0, 
        max_zoom=18,
        name = layer_name,
        overlay = True,
        control = True,
        attr = "Map Data &copy; <a href='https://earthengine.google.com/'>Google Earth Engine</a>",
    ).add_to(self)

#### Loading Power Plant database
This dataset is from the WRI (World Resources Institute) and it is also available as ee.FeatureCollection in Google Earth Engine. However, I got it on the WRI website and loaded it as a CSV file. Furthermore, i queried it on country code Mexico.

In [16]:
df = pd.read_csv('data/globalpowerplantdatabase/global_power_plant_database.csv')
df=df[df['country']=='MEX']

#### Adding Google Earth Engine Layer
Let's load an ee.Image object, which is in this case the World Population Layer of Mexico for the year 2020.

In [17]:
folium.Map.add_earth_engine_layer = add_earth_engine_layer

mx_pop_2020 = ee.Image('WorldPop/POP/MEX_2020')

vis = {'palette':['225ea8','41b6c4','a1dab4','ffffcc']}

m = folium.Map(location=[19.360843, -99.163400], zoom_start=7, height=500)

m.add_earth_engine_layer(mx_pop_2020, vis, mx_pop_2020.getInfo()['properties']['system:index'])

#### Adding Power Plant database layer
Here we are loading the power plant database layer from our Pandas DataFrame. It is filtered on Hydro and Biomass power plants. Icons come from **Freepik** and **photo3idea_studio**, downloaded from www.flaticon.com

In [18]:
powerplants = folium.map.FeatureGroup()
latitudes = list(df.latitude)
longitudes = list(df.longitude)
labels = list(df.primary_fuel)
capacity_mw = list(df.capacity_mw)
for lat, lng, label, capacity in zip(latitudes, longitudes, labels, capacity_mw):
    if label == 'Hydro':
        folium.Marker(
            location = [lat, lng], 
            popup = str(label)+': '+str(capacity),
            icon = folium.features.CustomIcon('src/icons/hydro-power.png',icon_size=(35, 35))
            # Icon made by Freepik from www.flaticon.com
        ).add_to(m) 
    if label == 'Biomass':
        folium.Marker(
            location = [lat, lng],
            popup = str(label)+': '+str(capacity),
            icon = folium.features.CustomIcon('src/icons/biomass.png',icon_size=(35, 35))
            # Icon made by photo3idea_studio from www.flaticon.com
        ).add_to(m)

#### Visualize everything together

In [19]:
m.add_child(folium.LayerControl())
m